# S&S 22 powell Calibration

In [2]:
import pandas as pd
import numpy as np
import random
from numpy.random import RandomState
from scipy import stats
from scipy.optimize import minimize
import scipy
import os
os.environ['R_HOME'] = '/Library/Frameworks/R.framework/Versions/4.1/Resources/'
import rpy2
from rpy2.robjects.packages import importr
from rpy2.robjects.packages import SignatureTranslatedAnonymousPackage
import datetime
from rpy2.robjects.vectors import FloatVector
from statsmodels.tsa.stattools import adfuller
from sklearn.linear_model import LinearRegression

np.random.seed(22101)

yuima = importr("yuima")
n_stvol_sim_string = """
n_stvol = function(random_seed, num_sim,
                    mu11, mu21, mu22, mu31, mu41, mu42, 
                    sigma11, sigma12, sigma13, sigma14,
                    sigma21, sigma22, sigma23, sigma24,
                    sigma31, sigma32, sigma33, sigma34,
                    sigma41, sigma42, sigma43, sigma44,
                    xinit_vec, vinit_vec, T0, T, length){
  
  set.seed(random_seed)
  
  drift = c("mu11*X1", "mu21-mu22*v1", "mu31*X2", "mu41-mu42*v2")
  diffusion = matrix(c("v1*X1*sigma11", "v1*X1*sigma12", "v1*X1*sigma13", "v1*X1*sigma14", 
                       "sigma21", "sigma22", "sigma23", "sigma24", 
                       "v2*X2*sigma31", "v2*X2*sigma32", "v2*X2*sigma33", "v2*X2*sigma34", 
                       "sigma41", "sigma42", "sigma43", "sigma44"), 
                     4, 4, byrow=TRUE)
  
  stvol_model = setModel(drift=drift, diffusion=diffusion,
                          time.variable = "t",
                          state.variable=c("X1", "v1", "X2", "v2"),
                          solve.variable=c("X1", "v1", "X2", "v2"))
  newsamp = setSampling(Initial=T0, Terminal=T, n=length)
  
  n_sim_data = data.frame(matrix(nrow=length+1, ncol=2*num_sim))
  for (i in 1:num_sim){
    stvol_sim = simulate(stvol_model, 
                          true.par=list(
                            mu11=mu11, mu21=mu21, mu22=mu22, mu31=mu31, mu41=mu41, mu42=mu42,  
                            sigma11=sigma11, sigma12=sigma12, sigma13=sigma13, sigma14=sigma14,
                            sigma21=sigma21, sigma22=sigma22, sigma23=sigma23, sigma24=sigma24,
                            sigma31=sigma31, sigma32=sigma32, sigma33=sigma33, sigma34=sigma34,
                            sigma41=sigma41, sigma42=sigma42, sigma43=sigma43, sigma44=sigma44), 
                          xinit=c(xinit_vec[[i]][1], vinit_vec[[i]][1], xinit_vec[[i]][2], vinit_vec[[i]][2]), 
                          sampling=newsamp)
    original_data = stvol_sim@data@original.data
    one_sim_stvol = data.frame(original_data[,1], original_data[,3])
    colnames(one_sim_stvol) = c('series1', 'series2')
    n_sim_data[, (2*i-1):(2*i)] = one_sim_stvol
  }
  return(n_sim_data)
}
"""

n_stvol_sim = SignatureTranslatedAnonymousPackage(n_stvol_sim_string, "n_stvol_sim")
def n_stvol_simulation(random_seed, num_sim,
                        mu11, mu21, mu22, mu31, mu41, mu42, 
                        sigma11, sigma12, sigma13, sigma14,
                        sigma21, sigma22, sigma23, sigma24,
                        sigma31, sigma32, sigma33, sigma34,
                        sigma41, sigma42, sigma43, sigma44,
                        xinit_vec, vinit_vec, T0, T, length):

    n_sim_data = pd.DataFrame(
        n_stvol_sim.n_stvol(random_seed=random_seed, num_sim=num_sim,
                              mu11=mu11, mu21=mu21, mu22=mu22, mu31=mu31, mu41=mu41, mu42=mu42,  
                              sigma11=sigma11, sigma12=sigma12, sigma13=sigma13, sigma14=sigma14,
                              sigma21=sigma21, sigma22=sigma22, sigma23=sigma23, sigma24=sigma24,
                              sigma31=sigma31, sigma32=sigma32, sigma33=sigma33, sigma34=sigma34,
                              sigma41=sigma41, sigma42=sigma42, sigma43=sigma43, sigma44=sigma44,
                              xinit_vec=xinit_vec, vinit_vec=vinit_vec, T0=T0, T=T, length=length)).transpose()
    return n_sim_data


def price_to_log_price(n_price):
    return(np.log(n_price))

def log_price_to_price(n_log_price):
    return(np.exp(n_log_price))

def price_to_return(n_price):
    n_return = pd.DataFrame()
    for i in range(n_price.shape[1]):
        ith_column_price_series = n_price.iloc[:, i]
        n_return = pd.concat([n_return, 100 * (np.log(ith_column_price_series[1:].values) - np.log(ith_column_price_series[:-1]))], axis=1)
    return n_return

def log_price_to_return(n_log_price):
    n_real_return = pd.DataFrame()
    for i in range(n_log_price.shape[1]):
        ith_column_price_series = n_log_price.iloc[:, i]
        n_real_return = pd.concat([n_real_return, 100 * (ith_column_price_series[1:].values - ith_column_price_series[:-1])], axis=1)
    return n_real_return

def cross_corr_coef(lag_time_series, lead_time_series, lag):
    # calculate the cross correlation between two time series
    # if the result is not zero, then 'lead_time_series' leads 'lag_time_series'
    lag_time_series = lag_time_series.iloc[lag:]
    corr_coef = np.corrcoef(lag_time_series, lead_time_series.iloc[0:((lead_time_series.size)-lag)])[0][1]
    return corr_coef
    
def cal_stats(n_return, n_price):
    
    return_series1 = n_return.iloc[:, ::2]
    return_series2 = n_return.iloc[:, 1::2]
    price_series1 = n_price.iloc[:, ::2]
    price_series2 = n_price.iloc[:, 1::2]

    
    mean1 = return_series1.mean(axis=0).values
    sd1 = return_series1.std(axis=0).values
    skew1 = return_series1.skew(axis=0).values
    kurtosis1 = return_series1.kurtosis(axis=0).values
    autocorr1 = return_series1.apply(lambda x: x.autocorr(lag=1))    
    
    
    mean2 = return_series2.mean(axis=0).values
    sd2 = return_series2.std(axis=0).values
    skew2 = return_series1.skew(axis=0).values
    kurtosis2 = return_series2.kurtosis(axis=0).values
    autocorr2 = return_series2.apply(lambda x: x.autocorr(lag=1)) 
    
    
    # Cross-correlation between return series
    corr_ts1_lag_0 = []
    corr_ts1_lag_1 = [] # if not zero, return series 2 leads return series 1
    corr_ts1_lag_2 = []
    corr_ts1_lag_3 = []
    corr_ts2_lag_1 = [] # if not zero, return series 1 lead return series 2
    corr_ts2_lag_2 = []
    corr_ts2_lag_3 = []
    for i in range(248):
        corr_ts1_lag_0.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 0))
        corr_ts1_lag_1.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 1))
        corr_ts1_lag_2.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 2))
        corr_ts1_lag_3.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 3))
        corr_ts2_lag_1.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 1))
        corr_ts2_lag_2.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 2))
        corr_ts2_lag_3.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 3))
    corr_ts1_lag_0 = pd.Series(corr_ts1_lag_0)
    corr_ts1_lag_1 = pd.Series(corr_ts1_lag_1)
    corr_ts1_lag_2 = pd.Series(corr_ts1_lag_2)
    corr_ts1_lag_3 = pd.Series(corr_ts1_lag_3)
    corr_ts2_lag_1 = pd.Series(corr_ts2_lag_1)
    corr_ts2_lag_2 = pd.Series(corr_ts2_lag_2)
    corr_ts2_lag_3 = pd.Series(corr_ts2_lag_3)
    
    
    # adf test on original prices: test if the price difference of the two time series is stationary
    p_values = []
    for i in range(248):
        reg = LinearRegression().fit(np.array(price_series1.iloc[:, i]).reshape((-1, 1)), np.array(price_series2.iloc[:, i]))
        y_pred = reg.predict(np.array(price_series1.iloc[:, i]).reshape((-1, 1)))
        res = np.array(price_series2.iloc[:, i]) - y_pred
        adf_result = adfuller(res)[1]
        p_values.append(adf_result)
    p_values = pd.Series(p_values)
    
    
    stats_data = pd.DataFrame([mean1, mean2, sd1, sd2, 
                               skew1, skew2, kurtosis1, kurtosis2, 
                               autocorr1, autocorr2, corr_ts1_lag_0, 
                               corr_ts1_lag_1, corr_ts1_lag_2, corr_ts1_lag_3,
                               corr_ts2_lag_1, corr_ts2_lag_2, corr_ts2_lag_3,
                               p_values])
    stats_data = stats_data.transpose()
    stats_data.columns = [
        'return_mean1', 'return_mean2',
        'return_sd1', 'return_sd2',
        'return_skew1', 'return_skew2',
        'return_kurtosis1', 'return_kurtosis2',
        'return_autocorrelation1', 'return_autocorrelation2',
        'return_correlation_ts1_lag_0',
        'return_correlation_ts1_lag_1', 'return_correlation_ts1_lag_2', 'return_correlation_ts1_lag_3',
        'return_correlation_ts2_lag_1', 'return_correlation_ts2_lag_2', 'return_correlation_ts2_lag_3',
        'price_adf_p_values']
    return stats_data



def loss_function(params):
    
    params = FloatVector(params)
    print(params)
    moment_loss = pd.DataFrame().reindex_like(real_stats)
    
    print(int(np.random.randint(low=0, high=980608, size=(1,))))
    print(int(np.random.randint(low=0, high=980608, size=(1,))))
    n_sim_price = n_stvol_simulation(
        random_seed=int(np.random.randint(low=0, high=980608, size=(1,))), num_sim=num_sim,
        mu11=params[0], mu21=params[1], mu22=params[2], mu31=params[3], mu41=params[4], mu42=params[5],  
        sigma11=params[6], sigma12=params[7], sigma13=params[8], sigma14=params[9],
        sigma21=params[10], sigma22=params[11], sigma23=params[12], sigma24=params[13],
        sigma31=params[14], sigma32=params[15], sigma33=params[16], sigma34=params[17],
        sigma41=params[18], sigma42=params[19], sigma43=params[20], sigma44=params[21],
        xinit_vec=xinit_vec, vinit_vec=vinit_vec, T0=T0, T=T, length=length)
    
    n_sim_return = price_to_return(n_sim_price)
    n_sim_stats = cal_stats(n_return=n_sim_return, n_price=n_sim_price)


    for i in range(n_real_stats.shape[0]):
        for j in range(n_real_stats.shape[1]):
            moment_loss.iloc[i, j] = np.sqrt((n_real_stats.iloc[i, j] - n_sim_stats.iloc[i, j])**2)
    sum_all = np.sum(moment_loss)
    print(sum_all)
    print(np.sum(sum_all))
    print('----------')

    return np.sum(sum_all)



real_price = pd.read_csv("sp500_20180101_20181231_pair_prices.csv", index_col=[0])
real_return = pd.read_csv("sp500_20180101_20181231_pair_returns.csv", index_col=[0])
real_stats = cal_stats(n_return=real_return, n_price=real_price)


xinit_vec = []
vinit_vec = []
for i in range(int(real_price.shape[1]/2)):
    init_pair_price = [real_price.iloc[0, 2*i], real_price.iloc[0, 2*i+1]]
    init_pair_price = FloatVector(init_pair_price)
    xinit_vec.append(init_pair_price)
    
    init_pair_volatility = [np.std(real_return.iloc[:, 2*i]/100), np.std(real_return.iloc[:, 2*i+1]/100)]
    init_pair_volatility = FloatVector(init_pair_volatility)
    vinit_vec.append(init_pair_volatility)
    
    
    
num_sim, T0, T, length = real_stats.shape[0], 0, 1, real_price.shape[0]

n_real_stats = real_stats




initial0 = [0.1, 1, 1, 0.1, 1, 1,
            0.1, 0.1, 0.1, 0.1,
            0.1, 0.1, 0.1, 0.1,
            0.1, 0.1, 0.1, 0.1,
            0.1, 0.1, 0.1, 0.1]

begin_time = datetime.datetime.now()
res = minimize(loss_function, initial0, method='Powell',
               tol=1e-6, options={'disp': True},
               bounds=[(None, None), (None, None), (None, None), (None, None), (None, None), (None, None),
                       (0, None), (0, None), (0, None), (0, None),
                       (0, None), (0, None), (0, None), (0, None),
                       (0, None), (0, None), (0, None), (0, None),
                       (0, None), (0, None), (0, None), (0, None)])
print(res.x)

time = datetime.datetime.now() - begin_time
print(time)

params = (res.x)
loss = loss_function((params))
print(loss)


 [1] 0.1 1.0 1.0 0.1 1.0 1.0 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1
[20] 0.1 0.1 0.1

450452
97804
return_mean1                      23.647705
return_mean2                      24.556237
return_sd1                       298.612003
return_sd2                       312.420203
return_skew1                     167.925849
return_skew2                     167.925849
return_kurtosis1                 861.504680
return_kurtosis2                1389.154184
return_autocorrelation1           19.297986
return_autocorrelation2           21.263431
return_correlation_ts1_lag_0     157.643035
return_correlation_ts1_lag_1      19.777175
return_correlation_ts1_lag_2      19.767801
return_correlation_ts1_lag_3      22.658806
return_correlation_ts2_lag_1      20.883222
return_correlation_ts2_lag_2      20.779933
return_correlation_ts2_lag_3      22.326719
price_adf_p_values                70.437220
dtype: float64
3640.582038243132
----------
 [1] 0.1 1.0 1.0 0.1 1.0 1.0 0.1 0.1 0.1 0.1 0.1 0.1

return_mean1                      32.998690
return_mean2                      24.914659
return_sd1                       297.184836
return_sd2                       310.907182
return_skew1                     152.998426
return_skew2                     152.998426
return_kurtosis1                 834.956248
return_kurtosis2                1418.679823
return_autocorrelation1           21.223102
return_autocorrelation2           21.877030
return_correlation_ts1_lag_0     157.644442
return_correlation_ts1_lag_1      20.389266
return_correlation_ts1_lag_2      19.980841
return_correlation_ts1_lag_3      22.586185
return_correlation_ts2_lag_1      21.482465
return_correlation_ts2_lag_2      22.065756
return_correlation_ts2_lag_3      22.599807
price_adf_p_values                90.319752
dtype: float64
3645.8069344412097
----------
 [1] 0.1557281 1.0000000 1.0000000 0.1000000 1.0000000 1.0000000 0.1000000
 [8] 0.1000000 0.1000000 0.1000000 0.1000000 0.1000000 0.1000000 0.1000000
[15] 0.100000

return_mean1                      28.061754
return_mean2                      26.461182
return_sd1                       295.929262
return_sd2                       309.704418
return_skew1                     164.544256
return_skew2                     164.544256
return_kurtosis1                 845.461272
return_kurtosis2                1374.156519
return_autocorrelation1           21.255648
return_autocorrelation2           19.643613
return_correlation_ts1_lag_0     157.645134
return_correlation_ts1_lag_1      19.759095
return_correlation_ts1_lag_2      19.889056
return_correlation_ts1_lag_3      22.468510
return_correlation_ts2_lag_1      22.228492
return_correlation_ts2_lag_2      19.699796
return_correlation_ts2_lag_3      20.970768
price_adf_p_values               104.520997
dtype: float64
3636.944028943407
----------
 [1] 0.1557486 1.0000000 1.0000000 0.1000000 1.0000000 1.0000000 0.1000000
 [8] 0.1000000 0.1000000 0.1000000 0.1000000 0.1000000 0.1000000 0.1000000
[15] 0.1000000

return_mean1                      30.429003
return_mean2                      24.978624
return_sd1                       111.026247
return_sd2                       313.586370
return_skew1                     159.574886
return_skew2                     159.574886
return_kurtosis1                 818.452247
return_kurtosis2                1395.057221
return_autocorrelation1           20.567263
return_autocorrelation2           21.624124
return_correlation_ts1_lag_0     156.316561
return_correlation_ts1_lag_1      20.265550
return_correlation_ts1_lag_2      22.139909
return_correlation_ts1_lag_3      19.629547
return_correlation_ts2_lag_1      21.037025
return_correlation_ts2_lag_2      19.775779
return_correlation_ts2_lag_3      20.806659
price_adf_p_values               115.599368
dtype: float64
3450.441266234702
----------
 [1] 0.1557281 3.1938954 1.0000000 0.1000000 1.0000000 1.0000000 0.1000000
 [8] 0.1000000 0.1000000 0.1000000 0.1000000 0.1000000 0.1000000 0.1000000
[15] 0.1000000

return_mean1                      32.437178
return_mean2                      25.013208
return_sd1                        94.280547
return_sd2                       310.304695
return_skew1                     160.662751
return_skew2                     160.662751
return_kurtosis1                 812.932302
return_kurtosis2                1393.125835
return_autocorrelation1           20.335834
return_autocorrelation2           21.645281
return_correlation_ts1_lag_0     156.443259
return_correlation_ts1_lag_1      20.700960
return_correlation_ts1_lag_2      20.361285
return_correlation_ts1_lag_3      20.879238
return_correlation_ts2_lag_1      21.563202
return_correlation_ts2_lag_2      20.413566
return_correlation_ts2_lag_3      21.742484
price_adf_p_values               121.185137
dtype: float64
3434.6895116630894
----------
 [1] 0.1557281 2.9173594 1.0000000 0.1000000 1.0000000 1.0000000 0.1000000
 [8] 0.1000000 0.1000000 0.1000000 0.1000000 0.1000000 0.1000000 0.1000000
[15] 0.100000

...

return_mean1                      64.453890
return_mean2                      92.209781
return_sd1                       260.013023
return_sd2                       758.273604
return_skew1                     158.955180
return_skew2                     158.955180
return_kurtosis1                 854.360499
return_kurtosis2                1391.492921
return_autocorrelation1           21.964692
return_autocorrelation2           20.890731
return_correlation_ts1_lag_0     102.244319
return_correlation_ts1_lag_1      19.257067
return_correlation_ts1_lag_2      19.373539
return_correlation_ts1_lag_3      20.393164
return_correlation_ts2_lag_1      20.285880
return_correlation_ts2_lag_2      21.504759
return_correlation_ts2_lag_3      20.484341
price_adf_p_values                84.571435
dtype: float64
4089.6840053715264
----------
 [1]  0.62786403  3.15289884  1.07235752 -0.62632353  1.61974370  0.08038954
 [7]  0.02924666  0.15938187  0.17653882  0.16431774  0.49148549  0.48706967
[13]  0.7

return_mean1                      60.505930
return_mean2                      96.484047
return_sd1                       258.784752
return_sd2                       741.608320
return_skew1                     161.249002
return_skew2                     161.249002
return_kurtosis1                 806.580321
return_kurtosis2                1359.310357
return_autocorrelation1           19.868751
return_autocorrelation2           22.726055
return_correlation_ts1_lag_0     101.044807
return_correlation_ts1_lag_1      18.112216
return_correlation_ts1_lag_2      18.585688
return_correlation_ts1_lag_3      21.377193
return_correlation_ts2_lag_1      22.052977
return_correlation_ts2_lag_2      21.137172
return_correlation_ts2_lag_3      22.433196
price_adf_p_values                79.399158
dtype: float64
3992.5089444520568
----------
 [1]  0.62786403  3.15289884  1.07235752 -0.62632353  1.61974370  0.08038954
 [7]  0.02924666  0.15938187  0.17653882  0.16431774  0.49148549  0.48706967
[13]  0.7

return_mean1                      63.788410
return_mean2                     101.391838
return_sd1                       241.200453
return_sd2                       774.871821
return_skew1                     160.386875
return_skew2                     160.386875
return_kurtosis1                 907.254251
return_kurtosis2                1380.455982
return_autocorrelation1           20.054922
return_autocorrelation2           20.327162
return_correlation_ts1_lag_0      98.898422
return_correlation_ts1_lag_1      19.189938
return_correlation_ts1_lag_2      19.689935
return_correlation_ts1_lag_3      21.329925
return_correlation_ts2_lag_1      20.956886
return_correlation_ts2_lag_2      20.034095
return_correlation_ts2_lag_3      21.872449
price_adf_p_values                82.389698
dtype: float64
4134.4799380795885
----------
 [1]  0.62786403  3.15289884  1.07235752 -0.62632353  1.61974370  0.08038954
 [7]  0.02924666  0.15938187  0.17653882  0.16431774  0.49148549  0.48706967
[13]  0.7

return_mean1                      63.164562
return_mean2                      86.499251
return_sd1                       255.932848
return_sd2                       657.833582
return_skew1                     156.996874
return_skew2                     156.996874
return_kurtosis1                 836.305639
return_kurtosis2                1431.604386
return_autocorrelation1           19.658791
return_autocorrelation2           20.798920
return_correlation_ts1_lag_0     101.170033
return_correlation_ts1_lag_1      20.239592
return_correlation_ts1_lag_2      19.325160
return_correlation_ts1_lag_3      21.656138
return_correlation_ts2_lag_1      21.835303
return_correlation_ts2_lag_2      21.776420
return_correlation_ts2_lag_3      22.016659
price_adf_p_values                91.342383
dtype: float64
4005.1534150334974
----------
 [1]  0.62786403  3.15289884  1.07235752 -0.62632353  1.61974370  0.08038954
 [7]  0.02924666  0.15938187  0.17653882  0.16431774  0.49148549  0.48706967
[13]  0.7

return_mean1                      63.155268
return_mean2                      84.622721
return_sd1                       252.010452
return_sd2                       634.550938
return_skew1                     153.693076
return_skew2                     153.693076
return_kurtosis1                 865.761572
return_kurtosis2                1358.320342
return_autocorrelation1           19.543630
return_autocorrelation2           21.894802
return_correlation_ts1_lag_0      96.977659
return_correlation_ts1_lag_1      21.286348
return_correlation_ts1_lag_2      20.444283
return_correlation_ts1_lag_3      22.086248
return_correlation_ts2_lag_1      21.214422
return_correlation_ts2_lag_2      20.881383
return_correlation_ts2_lag_3      22.526375
price_adf_p_values                85.173028
dtype: float64
3917.8356257450087
----------
3917.8356257450087


# Classification

In [8]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import random
from numpy.random import RandomState
from sklearn.linear_model import LinearRegression
from statsmodels.tsa.stattools import adfuller
from scipy import signal
from scipy import stats
from statsmodels.tsa.api import VAR
from statsmodels.tools.eval_measures import rmse, aic
import pickle
from statsmodels.stats.stattools import durbin_watson
import statsmodels.tsa.stattools as ts
from statsmodels.tsa.stattools import grangercausalitytests
from sklearn.model_selection import train_test_split
from supervised.automl import AutoML
from sklearn.metrics import accuracy_score
from supervised.preprocessing.eda import EDA

def cross_corr_coef(lag_time_series, lead_time_series, lag):
    # calculate the cross correlation between two time series
    # if the result is not zero, then 'lead_time_series' leads 'lag_time_series'

    lag_time_series = lag_time_series.iloc[lag:]
    corr_coef = np.corrcoef(lag_time_series, lead_time_series.iloc[0:((lead_time_series.size)-lag)])[0][1]

    return corr_coef

def create_statistics(label, rolling_window, return_csv_location, price_csv_location):

    return_df = pd.read_csv(return_csv_location, index_col=[0])
    return_df_series1 = return_df.iloc[:, ::2]
    return_df_series2 = return_df.iloc[:, 1::2]

    return_mean1 = return_df_series1.mean(axis=0)
    sd1 = return_df_series1.std(axis=0)
    skew1 = return_df_series1.skew(axis=0)
    kurtosis1 = return_df_series1.kurtosis(axis=0)
    autocorrelation_return1 = return_df_series1.apply(lambda x: x.autocorr(lag=1))
    rolling_window = rolling_window
    rolling_return_sd1 = return_df_series1.apply(lambda x: x.rolling(rolling_window).std()).iloc[rolling_window + 1:]
    autocorrelation_return_rolling_sd1 = rolling_return_sd1.apply(lambda x: x.autocorr(lag=1))

    standardised_price_df1 = 100 * np.exp(return_df_series1.cumsum() / 100)
    standardised_price_df1.loc[-1] = list(np.full(len(standardised_price_df1.columns), 100))  # adding a row
    standardised_price_df1.index = standardised_price_df1.index + 1  # shifting index
    standardised_price_df1 = standardised_price_df1.sort_index()
    standardised_price_mean1 = np.array(standardised_price_df1.mean(axis=0))

    return_mean2 = return_df_series2.mean(axis=0)
    sd2 = return_df_series2.std(axis=0)
    skew2 = return_df_series2.skew(axis=0)
    kurtosis2 = return_df_series2.kurtosis(axis=0)
    autocorrelation_return2 = return_df_series2.apply(lambda x: x.autocorr(lag=1))
    rolling_return_sd2 = return_df_series2.apply(lambda x: x.rolling(rolling_window).std()).iloc[rolling_window + 1:]
    autocorrelation_return_rolling_sd2 = rolling_return_sd2.apply(lambda x: x.autocorr(lag=1))

    standardised_price_df2 = 100 * np.exp(return_df_series2.cumsum() / 100)
    standardised_price_df2.loc[-1] = list(np.full(len(standardised_price_df2.columns), 100))  # adding a row
    standardised_price_df2.index = standardised_price_df2.index + 1  # shifting index
    standardised_price_df2 = standardised_price_df2.sort_index()
    standardised_price_mean2 = np.array(standardised_price_df2.mean(axis=0))


    # adf test on original prices: test if the price difference of the two time series is stationary
    price_df = pd.read_csv(price_csv_location, index_col=[0])
    price_df_series1 = price_df.iloc[:, ::2]
    price_df_series2 = price_df.iloc[:, 1::2]
    p_values = []
    for i in range(248):
        reg = LinearRegression().fit(np.array(price_df_series1.iloc[:, i]).reshape((-1, 1)), np.array(price_df_series2.iloc[:, i]))
        y_pred = reg.predict(np.array(price_df_series1.iloc[:, i]).reshape((-1, 1)))
        res = np.array(price_df_series2.iloc[:, i]) - y_pred
        adf_result = adfuller(res)[1]
        p_values.append(adf_result)
    p_values = pd.Series(p_values)


    # Cross-correlation between return series
    corr_ts1_lag_0 = []
    corr_ts1_lag_1 = [] # if not zero, return series 2 leads return series 1
    corr_ts1_lag_2 = []
    corr_ts1_lag_3 = []
    corr_ts2_lag_1 = [] # if not zero, return series 1 lead return series 2
    corr_ts2_lag_2 = []
    corr_ts2_lag_3 = []
    for i in range(248):
        corr_ts1_lag_0.append(cross_corr_coef(return_df_series1.iloc[:, i], return_df_series2.iloc[:, i], 0))
        corr_ts1_lag_1.append(cross_corr_coef(return_df_series1.iloc[:, i], return_df_series2.iloc[:, i], 1))
        corr_ts1_lag_2.append(cross_corr_coef(return_df_series1.iloc[:, i], return_df_series2.iloc[:, i], 2))
        corr_ts1_lag_3.append(cross_corr_coef(return_df_series1.iloc[:, i], return_df_series2.iloc[:, i], 3))
        corr_ts2_lag_1.append(cross_corr_coef(return_df_series2.iloc[:, i], return_df_series1.iloc[:, i], 1))
        corr_ts2_lag_2.append(cross_corr_coef(return_df_series2.iloc[:, i], return_df_series1.iloc[:, i], 2))
        corr_ts2_lag_3.append(cross_corr_coef(return_df_series2.iloc[:, i], return_df_series1.iloc[:, i], 3))

    corr_ts1_lag_0 = pd.Series(corr_ts1_lag_0)
    corr_ts1_lag_1 = pd.Series(corr_ts1_lag_1)
    corr_ts1_lag_2 = pd.Series(corr_ts1_lag_2)
    corr_ts1_lag_3 = pd.Series(corr_ts1_lag_3)
    corr_ts2_lag_1 = pd.Series(corr_ts2_lag_1)
    corr_ts2_lag_2 = pd.Series(corr_ts2_lag_2)
    corr_ts2_lag_3 = pd.Series(corr_ts2_lag_3)


    ### Granger Causality test
    durbin_watson_statistic1 = []
    durbin_watson_statistic2 = []
    co_integration_statistic = []
    price2_granger_cause_price1 = []
    price1_granger_cause_price2 = []
    for i in range(248):
        ts1 = price_df_series1.iloc[:, i]
        ts2 = price_df_series2.iloc[:, i]
        bivariate_time_series = np.array(pd.DataFrame([ts1, ts2]).transpose())
        var_model = VAR(bivariate_time_series)
        var_result_aic = []

        for j in [1, 2, 3, 4, 5, 6, 7, 8, 9, 10]:
            var_model_fit = var_model.fit(j)
            var_result_aic.append(var_model_fit.aic)

        var_lag = np.where(var_result_aic == np.min(var_result_aic))[0][0] + 1
        our_var_model = VAR(bivariate_time_series)
        our_var_model_fitted = our_var_model.fit(var_lag)

        # durbin_watson_statistic detect the presence of autocorrelation at lag 1 in the residuals from the regression
        durbin_watson_statistic = durbin_watson(our_var_model_fitted.resid)
        durbin_watson_statistic1.append(durbin_watson_statistic[0])
        durbin_watson_statistic2.append(durbin_watson_statistic[1])

        # test if the two time series co-integrated
        co_integration_statistic.append(ts.coint(ts1, ts2)[1])

        # granger causality test, output p-value of the F-test
        # For price2_granger_cause_price1, if p-value is less than 0.05, ts2 granger causes ts1, that is, the past values of ts2 have a statistically significant effect on the current value of ts1
        bivariate_ts1_ts2 = np.array(pd.DataFrame([ts1, ts2]).transpose())
        bivariate_ts2_ts1 = np.array(pd.DataFrame([ts2, ts1]).transpose())
        price2_granger_cause_price1.append(grangercausalitytests(bivariate_ts1_ts2, [var_lag])[var_lag][0]["ssr_ftest"][1])
        price1_granger_cause_price2.append(grangercausalitytests(bivariate_ts2_ts1, [var_lag])[var_lag][0]["ssr_ftest"][1])

    durbin_watson_statistic1 = pd.Series(durbin_watson_statistic1)
    durbin_watson_statistic2 = pd.Series(durbin_watson_statistic2)
    co_integration_statistic = pd.Series(co_integration_statistic)
    price2_granger_cause_price1 = pd.Series(price2_granger_cause_price1)
    price1_granger_cause_price2 = pd.Series(price1_granger_cause_price2)


    ### create new statistics data frame
    new_statistics = pd.DataFrame([
        standardised_price_mean1, standardised_price_mean2,
        return_mean1, return_mean2,
        sd1, sd2,
        skew1, skew2,
        kurtosis1, kurtosis2,
        autocorrelation_return1, autocorrelation_return2,
        autocorrelation_return_rolling_sd1, autocorrelation_return_rolling_sd2,
        p_values,
        corr_ts1_lag_0,
        corr_ts1_lag_1, corr_ts1_lag_2, corr_ts1_lag_3,
        corr_ts2_lag_1, corr_ts2_lag_2, corr_ts2_lag_3,
        durbin_watson_statistic1, durbin_watson_statistic2, co_integration_statistic,
        price2_granger_cause_price1, price1_granger_cause_price2
        ])
    new_statistics = new_statistics.transpose()
    new_statistics.columns = [
        'standardised_price_mean1', 'standardised_price_mean2',
        'return_mean1', 'return_mean2',
        'return_sd1', 'return_sd2',
        'return_skew1', 'return_skew2',
        'return_kurtosis1', 'return_kurtosis2',
        'return_autocorrelation_lag1_1', 'return_autocorrelation_lag1_2',
        'return_autocorrelation_lag1_rolling_sd1', 'return_autocorrelation_lag1_rolling_sd2',
        'price_adf_p_values',
        'return_correlation_ts1_lag_0',
        'return_correlation_ts1_lag_1', 'return_correlation_ts1_lag_2', 'return_correlation_ts1_lag_3',
        'return_correlation_ts2_lag_1', 'return_correlation_ts2_lag_2', 'return_correlation_ts2_lag_3',
        'durbin_watson_statistic1', 'durbin_watson_statistic2', 'co_integration_statistic',
        'price2_granger_cause_price1', 'price1_granger_cause_price2']
    label_col_position = new_statistics.shape[1]
    new_statistics.insert(label_col_position, 'label', label, allow_duplicates=True)

    return new_statistics


In [10]:
np.random.seed(9868)
num_iter = 10
random_seeds = np.random.randint(low=0, high=980608, size=(num_iter,))
results = []


for iter in range(num_iter):
    
    random_seed = int(random_seeds[iter])
    print(random_seed)
    
    n_sim_pair_prices = n_stvol_simulation(
    random_seed=random_seed, num_sim=248,
    mu11=0.62786403, mu21=3.15289884, mu22=1.07235752, 
    mu31=-0.62632353, mu41=1.6197437, mu42=0.08038954,  
    sigma11=0.02924666, sigma12=0.15938187, sigma13=0.17653882, sigma14=0.16431774,
    sigma21=0.49148549, sigma22=0.48706967, sigma23=0.76008214, sigma24=0.74369493,
    sigma31=0.39169426, sigma32=0.16380447, sigma33=0.39231845, sigma34=0.24113087,
    sigma41=0.67744312, sigma42=0.83114531, sigma43=0.26546568, sigma44=0.23644206,
    xinit_vec=xinit_vec, vinit_vec=vinit_vec, T0=0, T=1, length=250)

    n_sim_pair_returns = price_to_return(n_price=n_sim_pair_prices)

    n_sim_pair_prices.to_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Calibration/Cluster jobs/ss22/n_sim_pair_prices.csv")
    n_sim_pair_returns.to_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Calibration/Cluster jobs/ss22/n_sim_pair_returns.csv")

    real_statistics = create_statistics(
        label="real", 
        rolling_window=20, 
        return_csv_location="/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/sp500_20180101_20181231_pair_returns.csv", 
        price_csv_location ="/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/sp500_20180101_20181231_pair_prices.csv")

    simulated_statistics = create_statistics(
        label="simulated", 
        rolling_window=20, 
        return_csv_location="/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Calibration/Cluster jobs/ss22/n_sim_pair_returns.csv", 
        price_csv_location ="/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Calibration/Cluster jobs/ss22/n_sim_pair_prices.csv")


    dataset = pd.concat([real_statistics, simulated_statistics])
    X = dataset.iloc[:, 0:27]
    y = dataset.iloc[:, 27]

    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=random_seed)
    automl = AutoML(eval_metric='accuracy')
    automl.fit(X_train, y_train)
    predictions = automl.predict(X_test)
    accuracy_result = accuracy_score(y_test, predictions)
    results.append(accuracy_result)
    print(f"Accuracy of predictions:  {accuracy_result:.3f}")

accuracy_average = np.mean(results)
accuracy_std = np.std(results)
print(accuracy_average)

421827

Granger Causality
number of lags (no zero) 1
ssr based F test:         F=0.9324  , p=0.3352  , df_denom=246, df_num=1
ssr based chi2 test:   chi2=0.9438  , p=0.3313  , df=1
likelihood ratio test: chi2=0.9420  , p=0.3318  , df=1
parameter F test:         F=0.9324  , p=0.3352  , df_denom=246, df_num=1

Granger Causality
number of lags (no zero) 1
ssr based F test:         F=8.7943  , p=0.0033  , df_denom=246, df_num=1
ssr based chi2 test:   chi2=8.9016  , p=0.0028  , df=1
likelihood ratio test: chi2=8.7462  , p=0.0031  , df=1
parameter F test:         F=8.7943  , p=0.0033  , df_denom=246, df_num=1

Granger Causality
number of lags (no zero) 1
ssr based F test:         F=0.1016  , p=0.7502  , df_denom=246, df_num=1
ssr based chi2 test:   chi2=0.1028  , p=0.7485  , df=1
likelihood ratio test: chi2=0.1028  , p=0.7485  , df=1
parameter F test:         F=0.1016  , p=0.7502  , df_denom=246, df_num=1

Granger Causality
number of lags (no zero) 1
ssr based F test:         F=1.2218  , p=0

ssr based F test:         F=2.5430  , p=0.1121  , df_denom=246, df_num=1
ssr based chi2 test:   chi2=2.5740  , p=0.1086  , df=1
likelihood ratio test: chi2=2.5608  , p=0.1095  , df=1
parameter F test:         F=2.5430  , p=0.1121  , df_denom=246, df_num=1

Granger Causality
number of lags (no zero) 1
ssr based F test:         F=4.4146  , p=0.0367  , df_denom=246, df_num=1
ssr based chi2 test:   chi2=4.4684  , p=0.0345  , df=1
likelihood ratio test: chi2=4.4288  , p=0.0353  , df=1
parameter F test:         F=4.4146  , p=0.0367  , df_denom=246, df_num=1

Granger Causality
number of lags (no zero) 1
ssr based F test:         F=8.1184  , p=0.0048  , df_denom=246, df_num=1
ssr based chi2 test:   chi2=8.2174  , p=0.0041  , df=1
likelihood ratio test: chi2=8.0847  , p=0.0045  , df=1
parameter F test:         F=8.1184  , p=0.0048  , df_denom=246, df_num=1

Granger Causality
number of lags (no zero) 1
ssr based F test:         F=2.0904  , p=0.1495  , df_denom=246, df_num=1
ssr based chi2 test: 


Granger Causality
number of lags (no zero) 1
ssr based F test:         F=0.0147  , p=0.9037  , df_denom=246, df_num=1
ssr based chi2 test:   chi2=0.0149  , p=0.9030  , df=1
likelihood ratio test: chi2=0.0148  , p=0.9030  , df=1
parameter F test:         F=0.0147  , p=0.9037  , df_denom=246, df_num=1

Granger Causality
number of lags (no zero) 1
ssr based F test:         F=0.0802  , p=0.7773  , df_denom=246, df_num=1
ssr based chi2 test:   chi2=0.0811  , p=0.7758  , df=1
likelihood ratio test: chi2=0.0811  , p=0.7758  , df=1
parameter F test:         F=0.0802  , p=0.7773  , df_denom=246, df_num=1

Granger Causality
number of lags (no zero) 1
ssr based F test:         F=1.0033  , p=0.3175  , df_denom=246, df_num=1
ssr based chi2 test:   chi2=1.0155  , p=0.3136  , df=1
likelihood ratio test: chi2=1.0135  , p=0.3141  , df=1
parameter F test:         F=1.0033  , p=0.3175  , df_denom=246, df_num=1

Granger Causality
number of lags (no zero) 1
ssr based F test:         F=1.8103  , p=0.1797  


Granger Causality
number of lags (no zero) 1
ssr based F test:         F=0.3369  , p=0.5622  , df_denom=246, df_num=1
ssr based chi2 test:   chi2=0.3410  , p=0.5593  , df=1
likelihood ratio test: chi2=0.3408  , p=0.5594  , df=1
parameter F test:         F=0.3369  , p=0.5622  , df_denom=246, df_num=1

Granger Causality
number of lags (no zero) 1
ssr based F test:         F=5.4108  , p=0.0208  , df_denom=246, df_num=1
ssr based chi2 test:   chi2=5.4768  , p=0.0193  , df=1
likelihood ratio test: chi2=5.4175  , p=0.0199  , df=1
parameter F test:         F=5.4108  , p=0.0208  , df_denom=246, df_num=1

Granger Causality
number of lags (no zero) 1
ssr based F test:         F=8.9249  , p=0.0031  , df_denom=246, df_num=1
ssr based chi2 test:   chi2=9.0337  , p=0.0027  , df=1
likelihood ratio test: chi2=8.8737  , p=0.0029  , df=1
parameter F test:         F=8.9249  , p=0.0031  , df_denom=246, df_num=1

Granger Causality
number of lags (no zero) 1
ssr based F test:         F=0.0312  , p=0.8599  


Granger Causality
number of lags (no zero) 1
ssr based F test:         F=0.8909  , p=0.3462  , df_denom=246, df_num=1
ssr based chi2 test:   chi2=0.9018  , p=0.3423  , df=1
likelihood ratio test: chi2=0.9002  , p=0.3427  , df=1
parameter F test:         F=0.8909  , p=0.3462  , df_denom=246, df_num=1

Granger Causality
number of lags (no zero) 1
ssr based F test:         F=0.2894  , p=0.5911  , df_denom=246, df_num=1
ssr based chi2 test:   chi2=0.2929  , p=0.5883  , df=1
likelihood ratio test: chi2=0.2928  , p=0.5885  , df=1
parameter F test:         F=0.2894  , p=0.5911  , df_denom=246, df_num=1

Granger Causality
number of lags (no zero) 1
ssr based F test:         F=0.7779  , p=0.3787  , df_denom=246, df_num=1
ssr based chi2 test:   chi2=0.7873  , p=0.3749  , df=1
likelihood ratio test: chi2=0.7861  , p=0.3753  , df=1
parameter F test:         F=0.7779  , p=0.3787  , df_denom=246, df_num=1

Granger Causality
number of lags (no zero) 1
ssr based F test:         F=3.4636  , p=0.0639  

...


Granger Causality
number of lags (no zero) 3
ssr based F test:         F=0.2501  , p=0.8612  , df_denom=241, df_num=3
ssr based chi2 test:   chi2=0.7720  , p=0.8561  , df=3
likelihood ratio test: chi2=0.7708  , p=0.8564  , df=3
parameter F test:         F=0.2501  , p=0.8612  , df_denom=241, df_num=3

Granger Causality
number of lags (no zero) 3
ssr based F test:         F=0.4016  , p=0.7520  , df_denom=241, df_num=3
ssr based chi2 test:   chi2=1.2399  , p=0.7435  , df=3
likelihood ratio test: chi2=1.2368  , p=0.7442  , df=3
parameter F test:         F=0.4016  , p=0.7520  , df_denom=241, df_num=3

Granger Causality
number of lags (no zero) 10
ssr based F test:         F=3.7327  , p=0.0001  , df_denom=220, df_num=10
ssr based chi2 test:   chi2=40.8899 , p=0.0000  , df=10
likelihood ratio test: chi2=37.7694 , p=0.0000  , df=10
parameter F test:         F=3.7327  , p=0.0001  , df_denom=220, df_num=10

Granger Causality
number of lags (no zero) 10
ssr based F test:         F=4.0710  , p=0.

ssr based F test:         F=0.8022  , p=0.3713  , df_denom=247, df_num=1
ssr based chi2 test:   chi2=0.8119  , p=0.3675  , df=1
likelihood ratio test: chi2=0.8106  , p=0.3679  , df=1
parameter F test:         F=0.8022  , p=0.3713  , df_denom=247, df_num=1

Granger Causality
number of lags (no zero) 1
ssr based F test:         F=3.3912  , p=0.0667  , df_denom=247, df_num=1
ssr based chi2 test:   chi2=3.4324  , p=0.0639  , df=1
likelihood ratio test: chi2=3.4091  , p=0.0648  , df=1
parameter F test:         F=3.3912  , p=0.0667  , df_denom=247, df_num=1

Granger Causality
number of lags (no zero) 1
ssr based F test:         F=0.8127  , p=0.3682  , df_denom=247, df_num=1
ssr based chi2 test:   chi2=0.8226  , p=0.3644  , df=1
likelihood ratio test: chi2=0.8212  , p=0.3648  , df=1
parameter F test:         F=0.8127  , p=0.3682  , df_denom=247, df_num=1

Granger Causality
number of lags (no zero) 1
ssr based F test:         F=0.6061  , p=0.4370  , df_denom=247, df_num=1
ssr based chi2 test: 

Pass the following variable as a keyword arg: x. From version 0.12, the only valid positional argument will be `data`, and passing other arguments without an explicit keyword will result in an error or misinterpretation.


AutoML steps: ['simple_algorithms', 'default_algorithms', 'ensemble']
* Step simple_algorithms will try to check up to 3 models
1_Baseline accuracy 0.505747 trained in 8.55 seconds
2_DecisionTree accuracy 0.988506 trained in 13.68 seconds
3_Linear accuracy 1.0 trained in 10.72 seconds
* Step default_algorithms will try to check up to 3 models
4_Default_Xgboost accuracy 1.0 trained in 11.18 seconds
5_Default_NeuralNetwork accuracy 0.977011 trained in 10.58 seconds
6_Default_RandomForest accuracy 1.0 trained in 15.08 seconds
* Step ensemble will try to check up to 1 model
Ensemble accuracy 1.0 trained in 0.36 seconds
AutoML fit time: 79.94 seconds
AutoML best model: 3_Linear
Accuracy of predictions:  1.000
0.9953020134228188


An input array is constant; the correlation coefficent is not defined.


In [11]:
results

[0.9932885906040269,
 1.0,
 0.9798657718120806,
 1.0,
 0.9932885906040269,
 0.9932885906040269,
 0.9932885906040269,
 1.0,
 1.0,
 1.0]

# Auxiliary

In [3]:
params = FloatVector(res.x)

n_sim_pair_prices = n_stvol_simulation(
    random_seed=9868, num_sim=248,
    mu11=params[0], mu21=params[1], mu22=params[2], 
    mu31=params[3], mu41=params[4], mu42=params[5],  
    sigma11=params[6], sigma12=params[7], sigma13=params[8], sigma14=params[9],
    sigma21=params[10], sigma22=params[11], sigma23=params[12], sigma24=params[13],
    sigma31=params[14], sigma32=params[15], sigma33=params[16], sigma34=params[17],
    sigma41=params[18], sigma42=params[19], sigma43=params[20], sigma44=params[21],
    xinit_vec=xinit_vec, vinit_vec=vinit_vec, T0=0, T=1, length=250)

n_sim_pair_returns = price_to_return(n_price=n_sim_pair_prices)

print(n_sim_pair_prices)
print(n_sim_pair_returns)

n_sim_pair_prices.to_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Calibration/Cluster jobs/ss22/n_sim_pair_prices.csv")
n_sim_pair_returns.to_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Calibration/Cluster jobs/ss22/n_sim_pair_returns.csv")


           0          1           2          3            4           5    \
0    41.248272  61.745342   82.004974  59.762306  1189.010010  151.329498   
1    41.353879  61.633471   82.207686  59.655361  1192.586219  151.107277   
2    41.465721  61.536838   82.330452  59.373587  1193.489312  149.988876   
3    41.517009  61.106116   82.552689  59.212615  1195.818776  149.600287   
4    41.591701  60.815834   82.769358  59.039882  1200.263961  150.260615   
..         ...        ...         ...        ...          ...         ...   
246  62.210957  41.485948  168.668666  24.281728  1516.352123   25.827604   
247  62.677562  42.495090  185.999131  31.165646  1528.071652   26.294271   
248  63.215918  46.796710  164.803029  22.709086  1529.539799   25.681302   
249  63.071704  42.739564  164.963082  24.226914  1496.115237   24.429599   
250  64.049361  44.949951  165.444172  21.768395  1509.258944   24.925286   

             6            7           8           9    ...         486  \
0